In [78]:
%cd ..


from bokeh.io import output_notebook, reset_output, show, save
from bokeh.models import Panel, Range1d
from bokeh.plotting import figure

from Analysis.utilities import *
try:
    reset_output()
    output_notebook()
except:
    output_notebook()


/home/dtic


Loading BokehJS ...

# Agreement Heatmaps -- Three Repetitions Using Four Participants
Here we want to visualize the heatmaps of the dualized hits observed from MORE THAN 1 repetitions

In other words,

1. Find the steps that were observed in more than half of the repetitions (from any participant, any hand) --> Observed  >= 6 times
2. Find the steps that were observed in less than half of the repetitions (from any participant) --> Observed < 6 times

In [14]:
regrouped_repetitions = get_repetitions_dict_separated_by_participant(
    root_path="./midi_files/Repetitions/tested_with_four_participants",
    regroup_by_master_id=True,
    participants_id = [1, 2, 3, 4]
)
# order dict as {master_id: [participant_1_rep1, ..., participant_1_rep4, ... participant_2_rep1, ...]}
reordered_data = {}
master_ids = list(regrouped_repetitions['Participant_1'].keys())
for master_id in master_ids:
    reordered_data[master_id] = []
    for participant_id in regrouped_repetitions.keys():
        reordered_data[master_id].append(regrouped_repetitions[participant_id][master_id])



Participant_1
Participant_2
Participant_3
Participant_4


In [86]:
use_single_bar_for_analysis = True

# split into two groups (agreement and disagreement)
from copy import deepcopy
agreement_dict = deepcopy(reordered_data)
disagreement_dict = deepcopy(reordered_data)
agreement_data = []
disagreement_data = []



hits_total_agreement = 0
hits_total_disagreement = 0
total_hits = 0

per_participant_total_hits = {1: 0, 2: 0, 3: 0, 4: 0}
per_participant_agreement_hits = {1: 0, 2: 0, 3: 0, 4: 0}
per_participant_disagreement_hits = {1: 0, 2: 0, 3: 0, 4: 0}

per_participant_agreement_locs = {1: [], 2: [], 3: [], 4: []}
per_participant_disagreement_locs = {1: [], 2: [], 3: [], 4: []}
overall_agreement_locs = []
overall_disagreement_locs = []

for master_id, repetitions_list in reordered_data.items():
    for participant_id, repetitions in enumerate(repetitions_list):
        # combine hands
        for repetition_ix, repetition in enumerate(repetitions):
            flat = repetition.flatten_voices(reduce_dim=True)[:, 0]
            # flat shape is (time step, )
            other_participant_ids = [i for i in range(4) if i != participant_id]
            other_participants_repetitions = [repetitions_list[i][repetition_ix] for i in other_participant_ids for repetition_ix in range(3)]
            other_participants_flats = np.array([repetition.flatten_voices(reduce_dim=True)[:, 0] for repetition in other_participants_repetitions]) # shape is (9, 32)

            for time_step in range(flat.shape[0]):

                mult_by = np.ones((32, 6))
                mult_by[time_step, :] = 0
                if flat[time_step] == 1:
                    total_hits += 1
                    per_participant_total_hits[participant_id + 1] += 1

                # check if majority of other participants match the current participant at this time step
                if np.sum(other_participants_flats[:, time_step] == flat[time_step]) >= other_participants_flats.shape[0] * 0.5:
                    # agreement -> hence shouldn't appear in disagreement data
                    data = disagreement_dict[master_id][participant_id][repetition_ix].hvo
                    disagreement_dict[master_id][participant_id][repetition_ix].hvo = data * mult_by
                    if flat[time_step] == 1:
                        hits_total_agreement += 1
                        per_participant_agreement_hits[participant_id + 1] += 1

                        if use_single_bar_for_analysis:
                            per_participant_agreement_locs[participant_id + 1].append(time_step % 16)
                            overall_agreement_locs.append(time_step % 16)
                        else:
                            per_participant_agreement_locs[participant_id + 1].append(time_step)
                            overall_agreement_locs.append(time_step)

                else:
                    # disagreement -> hence shouldn't appear in agreement data
                    data = agreement_dict[master_id][participant_id][repetition_ix].hvo
                    agreement_dict[master_id][participant_id][repetition_ix].hvo = data * mult_by
                    if flat[time_step] == 1:
                        hits_total_disagreement += 1
                        per_participant_disagreement_hits[participant_id + 1] += 1
                    if use_single_bar_for_analysis:
                        per_participant_disagreement_locs[participant_id + 1].append(time_step % 16)
                        overall_disagreement_locs.append(time_step % 16)
                    else:
                        per_participant_agreement_locs[participant_id + 1].append(time_step)
                        overall_disagreement_locs.append(time_step)

            agreement_data.append(agreement_dict[master_id][participant_id][repetition_ix])
            disagreement_data.append(disagreement_dict[master_id][participant_id][repetition_ix])

print("-"*100)
print(f"hits_total_agreement/total_hits: {hits_total_agreement}/{total_hits} = " + str(hits_total_agreement/total_hits))
for i in range(1, 5):
    print("-"*100)
    print(f"Participant {i} agreement/total: {per_participant_agreement_hits[i]}/{per_participant_total_hits[i]} = " + str(per_participant_agreement_hits[i]/per_participant_total_hits[i]))
print("-"*100)

----------------------------------------------------------------------------------------------------
hits_total_agreement/total_hits: 5689/6405 = 0.8882123341139735
----------------------------------------------------------------------------------------------------
Participant 1 agreement/total: 1384/1482 = 0.9338731443994602
----------------------------------------------------------------------------------------------------
Participant 2 agreement/total: 1488/1738 = 0.856156501726122
----------------------------------------------------------------------------------------------------
Participant 3 agreement/total: 1456/1740 = 0.8367816091954023
----------------------------------------------------------------------------------------------------
Participant 4 agreement/total: 1361/1445 = 0.9418685121107266
----------------------------------------------------------------------------------------------------


In [87]:
p = figure(width=700, height=200, toolbar_location=None,
           title="Ratio of Matching Hits Per Step Per Participant")

# use colors: light brown, light red, light grey, light orange
colors = ["#f4a582", "#ff6666", "#d3d3d3", "#888888"]
# Histogram with four bars
for participant_id in [1, 2, 3, 4]:
    bins = np.linspace(0, 16, 17)
    agreements = np.array(per_participant_agreement_locs[participant_id])
    disagreements = np.array(per_participant_disagreement_locs[participant_id])
    hist_agr, edges = np.histogram(agreements, density=False, bins=bins)
    hist_dis, _ = np.histogram(disagreements, density=False, bins=bins)
    hist = hist_agr / (hist_agr + hist_dis)
    p.quad(top=hist, bottom=0, left=edges[:-1]+0.2*(participant_id-1), right=edges[:-1]+0.2*participant_id,
             fill_color=colors[participant_id-1], line_color="white",
             legend_label=f"Participant {participant_id}")


# change x tick labels to 0, 4, 8, 12, 16, 20, 24, 28, 32 at 0.5, 1.5, 2.5, 3.5, 4.5, 5.5, 6.5, 7.5, 8.5
p.xaxis.ticker = [0., 4., 8., 12., 16., 20., 24., 28., 32.]
#p.xaxis.major_label_overrides = {0.24: '0', 4.5: '4', 8.5: '8', 12.5: '12', 16.5: '16', 20.5: '20', 24.5: '24', 28.5: '28', 32.5: '32'}
# place legend at top left (in a single row)
# place legend outside of plot
p.legend.location = "bottom"
p.legend.orientation = "horizontal"
p.legend.click_policy="hide"
p.legend.label_text_font_size = "10pt"
p.legend.spacing = 0
p.legend.glyph_height = 10
p.legend.glyph_width = 10
p.legend.label_height = 10
p.legend.label_width = 10
p.legend.margin = 0
p.legend.padding = 0

# adjust y range to -0.2, 1
p.y_range = Range1d(-0.2, 1.2)
p.yaxis.ticker = [0., 0.2, 0.4, 0.6, 0.8, 1.0]
p.yaxis.major_label_overrides = {0.0: '0', 0.2: '0.2', 0.4: '0.4', 0.6: '0.6', 0.8: '0.8', 1.0: '1.0'}
p.yaxis.axis_label = "Ratio of Matching Hits"
show(p)

In [16]:
## Mix Together
agreement_figs = get_heatmap_for_hvo_sequences(hvo_sequences=agreement_data, redo_y_labels=True, participant_ids=[1, 2, 3, 4])
disagreement_figs = get_heatmap_for_hvo_sequences(hvo_sequences=disagreement_data, redo_y_labels=True, participant_ids=[1, 2, 3, 4])
mixed_fig = Tabs(
    tabs=[
        Panel(child=agreement_figs , title="Agreement"),
        Panel(child=disagreement_figs , title="Disagreement"),
    ]
)
show(mixed_fig)